In [1]:
# Set up Dependencies
from progress.bar import IncrementalBar
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import requests
import time
import nltk
import json
import csv
import sys
import os
from scipy.stats import linregress
from pprint import pprint
from api_keys import api_key_omdb
from api_keys import tmdb_key

# Skip this section when re-running code - skip to "Start Here"
It takes ove 8 hours for this section of code to run.  The results of this code has been stored in files, so it does not need to be run again.

In [ ]:
# The Movie Database API base url for discovering movies (more filter parameter were available for this one)
tmdb_url = 'https://api.themoviedb.org/3/discover/movie'

# creating an empty list to hold the reulting ids from the API
tmdb_ids = []

# list of start dates to loop through for the API calls, because only 10,000 items were returned per call
dates = ['1990-01-01','1994-05-07','1998-03-31','2001-05-15','2003-08-22','2005-04-28','2006-12-20','2008-04-09',
         '2009-09-11','2010-12-12','2012-01-01','2013-01-01','2013-11-15','2014-10-01','2015-08-06',
         '2016-06-10','2017-04-16','2018-02-04','2018-12-07','2019-10-16']

# setup the filter parameters to select only theatrical movies that were released 1990 or later 
# with an original language of English, starting on page 1 of the results
params = {'api_key':tmdb_key,
          'language':'en-US',
          'include_adult':'false',
          'release_date.gte':'1990-01-01',
          'sort_by':'release_date.asc',
          'include_video':'false',
          'with_original_language':'en',
          'page':'1'}

# loop through all the start dates
for date in dates:
    # set the next start date in the parameters
    params['release_date.gte'] = date
    print(date)
    
    # send the API request with the current parameters
    response_json = requests.get(tmdb_url, params=params).json()
    
    # get the number of pages in the current API call return
    pages = response_json['total_pages']
    
    # loop through all the pages of the current API call return
    for page in range(2,pages):
        print(f'page: {page}')
        
        # loop through the 20 results on the current page
        for i in range(0,20):
            
            # add the tmdb id to the list of ids
            tmdb_ids.append(response_json['results'][i]['id'])
            print(f"{response_json['results'][i]['id']}")
        
        # set the parameter for the next page & make the next API call to process
        params['page'] = page
        response_json = requests.get(tmdb_url, params=params).json()
        
# print the number of ids acquired
len(tmdb_ids)

In [ ]:
# print the list of ids to a file so the above code does not have to be re-run
output_file = os.path.join('data_files','tmdb_id_list.txt')
# Open the text file for writing
with open(output_file, 'w', encoding='utf-8', newline='\n') as txtfile:

    # write the list data to the text file
    print(tmdb_ids, file=txtfile)

# Close the text file
txtfile.close()

In [8]:
# read the list in from the text file
input_file = os.path.join('data_files','tmdb_id_list.txt')
# Open the csv file for reading
with open(input_file, 'r', encoding='utf-8') as read_file:
    
    reader = csv.reader(read_file)
    tmdb_ids = list(reader)[0]
    
len(tmdb_ids)

191138

In [16]:
# break the list of ids into chunks, there are too many to process all at once
tmdb_id_chunks = [tmdb_ids[x:x+25000] for x in range(0, len(tmdb_ids), 25000)]
tmdb_id_chunks

8

In [30]:
# blank lists to hold the values form the API calls
budget = []
imdb_ids = []
revenue = []

# set the parameters for the call to The Movie Database API to get the data from the list of ids acquired above
params2 = {'api_key': tmdb_key,
          'language': 'en-US'}

# loop through the 8 chunks of data created in the previous cell
for i in range (0,8):
    # reset the counter to keep track of where the code is in the loop
    count=0
    
    # loop through all the ids in the current chunk
    for id in tmdb_id_chunks[i]:
        
        # increment the counter
        count+=1
        
        try:
            # create the base url for the current id
            url_2 = f'https://api.themoviedb.org/3/movie/{id}'
            print(f'{count}: {id}')
            
            # send the API call for the current id using the parameters
            response_json2 = requests.get(url_2, params=params2).json()
        
            # append the data to the appropriate list
            budget.append(response_json2['budget'])
            imdb_ids.append(response_json2['imdb_id'])
            revenue.append(response_json2['revenue'])
            
        except KeyError:
            print('missing data')
            pass
    
    #put into dataframe
    tmdb_df = pd.DataFrame(columns=['Budget', 'IMDB ID', 'Revenue'])
    tmdb_df['Budget'] = budget
    tmdb_df['IMDB ID'] = imdb_ids
    tmdb_df['Revenue'] = revenue
    
    # save the current chunk of data as a csv file
    output_data_file = os.path.join('data_files',f'tmdb_data{i}.csv')
    # Open the csv file for writing
    with open(output_data_file, 'w', encoding='utf-8', newline='\n') as csvfile:

        # write the DataFrame data to the csv file
        tmdb_df.to_csv(csvfile, index=False)

    # Close the csv file
    csvfile.close()

1:  321969
2:  321658
3:  278465
4:  252675
5:  216697
6:  150447
7:  109669
8:  69068
9:  33666
10:  26579
11:  19592
12:  11469
13:  10956
14:  8978
15:  702117
16:  385807
17:  336393
18:  80002
19:  61050
20:  46075
21:  41726
22:  41497
23:  14566
24:  14187
25:  11208
26:  10065
27:  9798
28:  3631
29:  1901
30:  559822
31:  501830
32:  474130
33:  397329
34:  340150
35:  229128
36:  84242
37:  59712
38:  48121
39:  45668
40:  39850
41:  36883
42:  30800
43:  29898
44:  25379
45:  24123
46:  21838
47:  15276
48:  13498
49:  12547
50:  10845
51:  10762
52:  10263
53:  10027
54:  9515
55:  9288
56:  1956
57:  187
58:  446028
59:  277966
60:  270016
61:  258040
62:  201521
63:  107305
64:  47514
65:  36589
66:  28416
67:  25033
68:  21078
69:  20215
70:  16456
71:  15184
72:  14358
73:  13468
74:  13416
75:  13374
76:  11099
77:  11045
78:  10320
79:  9981
80:  9667
81:  7870
82:  4836
83:  4379
84:  3989
85:  1894
86:  1665
87:  27
88:  708252
89:  524159
90:  342001
91:  321367
92

673:  383211
674:  376126
675:  318800
676:  294260
677:  277486
678:  275750
679:  272633
680:  177947
681:  142225
682:  141654
683:  105354
684:  76178
685:  58955
686:  51780
687:  46431
688:  43202
689:  32646
690:  17364
691:  13933
692:  13568
693:  9722
694:  2056
695:  709700
696:  507149
697:  479264
698:  466316
699:  443540
700:  383213
701:  172424
702:  165534
703:  53977
704:  25313
705:  14499
706:  13282
707:  10204
708:  6439
709:  501422
710:  345917
711:  299918
712:  294351
713:  223139
714:  42192
715:  41488
716:  40675
717:  13682
718:  5495
719:  1439
720:  922
721:  320
722:  605920
723:  423939
724:  375484
725:  337122
726:  337121
727:  337031
728:  337026
729:  337024
730:  336767
731:  332188
732:  218091
733:  192143
734:  129746
735:  77033
736:  59210
737:  25460
738:  24408
739:  15256
740:  11036
741:  1126
742:  693111
743:  692563
744:  608290
745:  540998
746:  381244
747:  362720
748:  354205
749:  337124
750:  337123
751:  337120
752:  337022
75

1306:  44900
1307:  37241
1308:  30451
1309:  25975
1310:  25312
1311:  25248
1312:  19109
1313:  14922
1314:  14885
1315:  14175
1316:  2108
1317:  641
1318:  580883
1319:  400670
1320:  328876
1321:  125565
1322:  110438
1323:  11453
1324:  553603
1325:  311425
1326:  218821
1327:  60071
1328:  53542
1329:  10696
1330:  457787
1331:  429587
1332:  244012
1333:  141642
1334:  49867
1335:  33005
1336:  14228
1337:  684565
1338:  607967
1339:  324516
1340:  267913
1341:  253666
1342:  208948
1343:  107591
1344:  67397
1345:  49771
1346:  44502
1347:  31541
1348:  25028
1349:  21450
1350:  16764
1351:  540358
1352:  431014
1353:  393010
1354:  365006
1355:  353886
1356:  274508
1357:  273136
1358:  57021
1359:  46358
1360:  41714
1361:  39914
1362:  34468
1363:  28522
1364:  24738
1365:  8878
1366:  5916
1367:  71
1368:  572193
1369:  507598
1370:  384945
1371:  382491
1372:  249884
1373:  245556
1374:  74968
1375:  9516
1376:  8292
1377:  6957
1378:  440718
1379:  424074
1380:  354121
1

1921:  50498
1922:  49622
1923:  48339
1924:  38583
1925:  10092
1926:  9885
1927:  9007
1928:  7182
1929:  4348
1930:  3291
1931:  1830
1932:  340
1933:  692931
1934:  588055
1935:  360235
1936:  319577
1937:  224790
1938:  4543
1939:  1690
1940:  444054
1941:  436613
1942:  361210
1943:  328117
1944:  310758
1945:  65359
1946:  36155
1947:  14266
1948:  9987
1949:  703792
1950:  578941
1951:  326516
1952:  311515
1953:  292950
1954:  121678
1955:  1995
1956:  554405
1957:  513063
1958:  412118
1959:  312392
1960:  300266
1961:  198580
1962:  154178
1963:  139484
1964:  132353
1965:  79291
1966:  47599
1967:  28280
1968:  10927
1969:  9040
1970:  9012
1971:  471835
1972:  356024
1973:  153175
1974:  130458
1975:  17388
1976:  11529
1977:  2924
1978:  2313
1979:  2287
1980:  717185
1981:  585140
1982:  493977
1983:  436612
1984:  405722
1985:  339947
1986:  284911
1987:  135657
1988:  71580
1989:  49415
1990:  46074
1991:  28107
1992:  15144
1993:  13746
1994:  11892
1995:  11814
1996:

2532:  72963
2533:  69373
2534:  65051
2535:  59832
2536:  57456
2537:  46003
2538:  41396
2539:  35683
2540:  25396
2541:  23133
2542:  16228
2543:  12591
2544:  710638
2545:  519492
2546:  356364
2547:  275928
2548:  172027
2549:  138178
2550:  88870
2551:  64179
2552:  10110
2553:  116
2554:  431327
2555:  312660
2556:  190511
2557:  187286
2558:  185430
2559:  184587
2560:  27848
2561:  26985
2562:  15785
2563:  9968
2564:  9775
2565:  9583
2566:  25
2567:  707939
2568:  637016
2569:  572136
2570:  483914
2571:  443141
2572:  374022
2573:  365772
2574:  365771
2575:  341841
2576:  319327
2577:  314427
2578:  225298
2579:  221124
2580:  211539
2581:  206696
2582:  206013
2583:  106399
2584:  90295
2585:  49384
2586:  35223
2587:  24929
2588:  21274
2589:  19816
2590:  16028
2591:  12536
2592:  11773
2593:  3131
2594:  215
2595:  708370
2596:  707073
2597:  582682
2598:  521731
2599:  383691
2600:  307888
2601:  299700
2602:  244234
2603:  228434
2604:  73772
2605:  72942
2606:  1079

...

13736:  639428
13737:  639425
13738:  639417
13739:  639211
13740:  638993
13741:  638982
13742:  638977
13743:  638857
13744:  638770
13745:  638730
13746:  637960
13747:  637688
13748:  637680
13749:  635772
13750:  632023
13751:  631800
13752:  631795
13753:  631049
13754:  629745
13755:  629181
13756:  628038
13757:  627081
13758:  627079
13759:  625213
13760:  614869
13761:  614626
13762:  560981
13763:  507783
13764:  694024
13765:  680139
13766:  679106
13767:  669915
13768:  663926
13769:  661777
13770:  661395
13771:  660791
13772:  651967
13773:  650410
13774:  649141
13775:  645047
13776:  640519
13777:  639973
13778:  639392
13779:  639363
13780:  639361
13781:  639358
13782:  639254
13783:  639169
13784:  638966
13785:  637966
13786:  635771
13787:  631998
13788:  624384
13789:  624366
13790:  624365
13791:  624352
13792:  620988
13793:  616169
13794:  1955
13795:  717057
13796:  711829
13797:  670214
13798:  663755
13799:  652680
13800:  641557
13801:  641556
13802:  6403

14285:  665035
14286:  663199
14287:  662070
14288:  661345
14289:  660696
14290:  659515
14291:  653106
14292:  652333
14293:  650356
14294:  649231
14295:  648627
14296:  646245
14297:  644710
14298:  644036
14299:  644013
14300:  644012
14301:  643486
14302:  643025
14303:  643022
14304:  643014
14305:  643010
14306:  642980
14307:  642817
14308:  642772
14309:  642652
14310:  642641
14311:  642607
14312:  642354
14313:  642257
14314:  641989
14315:  641786
14316:  641710
14317:  641300
14318:  640173
14319:  640121
14320:  639923
14321:  638507
14322:  636709
14323:  636514
14324:  635710
14325:  635489
14326:  635100
14327:  633000
14328:  627465
14329:  621754
14330:  617773
14331:  612724
14332:  607217
14333:  597785
14334:  590121
14335:  590009
14336:  586592
14337:  584044
14338:  583525
14339:  580630
14340:  578189
14341:  560362
14342:  549214
14343:  543580
14344:  543025
14345:  528888
14346:  528644
14347:  522039
14348:  515402
14349:  515195
14350:  509598
14351:  50

14834:  522162
14835:  492188
14836:  489176
14837:  441282
14838:  714463
14839:  709796
14840:  697342
14841:  697145
14842:  690347
14843:  689349
14844:  682761
14845:  679763
14846:  672088
14847:  668347
14848:  666886
14849:  664933
14850:  648106
14851:  647496
14852:  646947
14853:  646945
14854:  646151
14855:  646000
14856:  642224
14857:  639979
14858:  639771
14859:  639372
14860:  636036
14861:  634576
14862:  630898
14863:  627879
14864:  623356
14865:  605900
14866:  594221
14867:  590531
14868:  579789
14869:  570352
14870:  564149
14871:  550648
14872:  550017
14873:  549053
14874:  541576
14875:  541099
14876:  532636
14877:  528091
14878:  525696
14879:  524348
14880:  520900
14881:  517517
14882:  508664
14883:  487291
14884:  480881
14885:  480042
14886:  479366
14887:  475351
14888:  470878
14889:  467956
14890:  451919
14891:  430474
14892:  330457
14893:  329205
14894:  295151
14895:  26371
14896:  714924
14897:  714667
14898:  714479
14899:  712249
14900:  710

15381:  642275
15382:  634571
15383:  628590
15384:  623953
15385:  612577
15386:  611207
15387:  604790
15388:  596962
15389:  575314
15390:  565377
15391:  549319
15392:  547090
15393:  521844
15394:  520360
15395:  506554
15396:  505205
15397:  502147
15398:  475214
15399:  369560
15400:  719972
15401:  695535
15402:  686383
15403:  684912
15404:  677208
15405:  666904
15406:  663910
15407:  663480
15408:  661828
15409:  661122
15410:  660856
15411:  659629
15412:  658087
15413:  656676
15414:  653673
15415:  652650
15416:  652341
15417:  650890
15418:  650581
15419:  650540
15420:  650287
15421:  650094
15422:  650017
15423:  649861
15424:  648408
15425:  648090
15426:  645971
15427:  644936
15428:  643807
15429:  640882
15430:  632346
15431:  629121
15432:  627469
15433:  627078
15434:  617933
15435:  611914
15436:  605509
15437:  594270
15438:  584973
15439:  582070
15440:  570488
15441:  568693
15442:  566220
15443:  553798
15444:  552178
15445:  535308
15446:  528761
15447:  50

15928:  700516
15929:  688286
15930:  681179
15931:  678371
15932:  661102
15933:  660324
15934:  659688
15935:  655667
15936:  655666
15937:  655665
15938:  655663
15939:  655660
15940:  655659
15941:  655658
15942:  655656
15943:  655047
15944:  654943
15945:  654671
15946:  654125
15947:  654035
15948:  651985
15949:  643938
15950:  630919
15951:  627477
15952:  626313
15953:  514277
15954:  331482
15955:  720745
15956:  718723
15957:  713965
15958:  710671
15959:  694588
15960:  693986
15961:  689347
15962:  685783
15963:  682043
15964:  666650
15965:  657412
15966:  656385
15967:  655355
15968:  654766
15969:  654741
15970:  654578
15971:  654081
15972:  653364
15973:  649233
15974:  644120
15975:  639409
15976:  627478
15977:  626309
15978:  625336
15979:  623338
15980:  509932
15981:  722768
15982:  710682
15983:  701614
15984:  692366
15985:  680244
15986:  676697
15987:  674745
15988:  673445
15989:  672256
15990:  668509
15991:  667043
15992:  663414
15993:  662374
15994:  65

In [4]:
# create the data frame to hold the data acquired from the API calls
tmdb_data_df = pd.DataFrame(columns=['Budget', 'IMDB ID', 'Revenue'])

# loop through the 8 data files that hold the chunks of data acquired
for j in range(0,8):
    
    # generate the path for the current chunk
    input_data_file = os.path.join('data_files', f'tmdb_data{j}.csv')
    
    # Open the csv file for reading
    with open(input_data_file, 'r', encoding='utf-8') as read_file:

        # read the data back into the DataFrame from the csv file
        input_data_df = pd.read_csv(read_file)
    
    # append the current chunk data frame to the overall dataframe
    tmdb_data_df = tmdb_data_df.append(input_data_df, ignore_index=True)

tmdb_data_df

Budget     IMDB ID Revenue
0           0         NaN       0
1           0         NaN       0
2           0         NaN       0
3           0   tt0295695       0
4           0         NaN       0
...       ...         ...     ...
566027      0  tt11983388       0
566028      0         NaN       0
566029      0   tt8997134       0
566030      0         NaN       0
566031      0         NaN       0

[566032 rows x 3 columns]

In [5]:
# drop any of the records from the data frame that contain a field with an N/A
filter_tmdb_data_df = tmdb_data_df.dropna()
filter_tmdb_data_df

Budget     IMDB ID Revenue
3           0   tt0295695       0
6           0   tt0243156       0
8           0  tt12495952       0
9           0   tt0150942       0
10          0   tt7610396       0
...       ...         ...     ...
566017      0  tt11472886       0
566018      0   tt8757908       0
566023      0  tt11465650       0
566027      0  tt11983388       0
566029      0   tt8997134       0

[424967 rows x 3 columns]

In [7]:
# filter the data frame to remove records that have a value of 0 for either Budget or Revenue
tmdb_data_filter_good_df = filter_tmdb_data_df.loc[(filter_tmdb_data_df['Budget'] > 0) & (filter_tmdb_data_df['Revenue'] > 0)]
tmdb_data_filter_good_df

Budget     IMDB ID    Revenue
614      7000000   tt0097758     793775
622     70000000   tt0096754   90000098
624      6000000   tt0091763  138530565
625     25000000   tt0095953  354825435
626     28000000   tt0092644  299965036
...          ...         ...        ...
565846   5000000   tt1773753     470901
565847  40000000   tt3281548  191540586
565941      1000  tt12098452       1080
565957   9000000   tt5827916    4612788
565994   2000000   tt1596753     650675

[39499 rows x 3 columns]

In [8]:
# Save the filtered data to a csv file
output_data_file = os.path.join('data_files','good_tmdb_data.csv')
# Open the csv file for writing
with open(output_data_file, 'w', encoding='utf-8', newline='\n') as csvfile:

    # write the DataFrame data to the csv file
    tmdb_data_filter_good_df.to_csv(csvfile, index=False)

# Close the csv file
csvfile.close()

# Start Here
The code from here forward is quick, but this section will require an API key.
Make sure to run the dependecy cell at the top, then start here for running code (cells before this will take WAY TOO LONG)

In [3]:
# read the data back into the dataframe from the csv file
input_data_file = os.path.join('data_files','good_tmdb_data.csv')

# Open the csv file for writing
with open(input_data_file, 'r', encoding='utf-8', newline='\n') as csvfile:

    # write the DataFrame data to the csv file
    tmdb_data_filter_good_df = pd.read_csv(csvfile)

# Close the csv file
csvfile.close()

# display dataframe to make sure it imported properly
tmdb_data_filter_good_df

Budget     IMDB ID    Revenue
0       7000000   tt0097758     793775
1      70000000   tt0096754   90000098
2       6000000   tt0091763  138530565
3      25000000   tt0095953  354825435
4      28000000   tt0092644  299965036
...         ...         ...        ...
39494   5000000   tt1773753     470901
39495  40000000   tt3281548  191540586
39496      1000  tt12098452       1080
39497   9000000   tt5827916    4612788
39498   2000000   tt1596753     650675

[39499 rows x 3 columns]

In [4]:
# filter out duplicates based on the IMDB ID
tmdb_data_clean_df = tmdb_data_filter_good_df.drop_duplicates(['IMDB ID'], keep='first', ignore_index=True)
tmdb_data_clean_df

Budget     IMDB ID    Revenue
0       7000000   tt0097758     793775
1      70000000   tt0096754   90000098
2       6000000   tt0091763  138530565
3      25000000   tt0095953  354825435
4      28000000   tt0092644  299965036
...         ...         ...        ...
5479  125000000   tt7975244  310830000
5480  100000000   tt5814534  171616764
5481    5000000   tt0083550   12534817
5482   40000000   tt3281548  191540586
5483       1000  tt12098452       1080

[5484 rows x 3 columns]

In [5]:
# check to make sure there are no duplicate ids
tmdb_data_clean_df['IMDB ID'].value_counts()

tt3454030    1
tt0473705    1
tt0120586    1
tt0469263    1
tt0432348    1
            ..
tt0107930    1
tt0101597    1
tt1931533    1
tt3104988    1
tt0362227    1
Name: IMDB ID, Length: 5484, dtype: int64

In [6]:
#This section will random select a number of ids to pull from the OMDB database
# set the range of random values based on the size of the dataframe so a list of random indexes can be generated
imdb_range = (0,len(tmdb_data_clean_df['IMDB ID']))

# Lists for holding IDs
call_ids = []
numbers=[]

# Setting a seed for the random number generator, so I end up with the same numbers every time I run the script
np.random.seed(369)

# Create a a list of random numbers that will be used as indexs of the movie dataframe
for count in range(1200):
    # generate a random number
    n = np.random.randint(imdb_range[0], imdb_range[1])
    
    # check to see if the number is already on the list, if it is not, then add it to the list
    if n not in numbers:
        numbers.append(n)

# for each index append the imdb ID (named tconst)
for number in numbers:
#     print(tmdb_data_filter_good_df.iloc[number][1])
    call_ids.append(tmdb_data_clean_df.iloc[number][1])
call_ids

['tt0071853',
 'tt0120467',
 'tt1206543',
 'tt0200550',
 'tt0127536',
 'tt0053125',
 'tt3416742',
 'tt1047540',
 'tt0350028',
 'tt1211956',
 'tt0113010',
 'tt1103982',
 'tt0454945',
 'tt0122933',
 'tt2526660',
 'tt4465564',
 'tt0796366',
 'tt0117665',
 'tt2638144',
 'tt0113677',
 'tt0207201',
 'tt0102685',
 'tt0075909',
 'tt1956620',
 'tt1134664',
 'tt3263904',
 'tt2381941',
 'tt2473682',
 'tt0042192',
 'tt1966359',
 'tt0161083',
 'tt0071562',
 'tt0242653',
 'tt0099329',
 'tt0096978',
 'tt1454468',
 'tt0421729',
 'tt0103074',
 'tt0944114',
 'tt2304517',
 'tt0373051',
 'tt0056197',
 'tt0102749',
 'tt0097027',
 'tt3322364',
 'tt0078346',
 'tt1155056',
 'tt2088003',
 'tt0065938',
 'tt0481536',
 'tt1662293',
 'tt0402901',
 'tt1034331',
 'tt1212428',
 'tt0421073',
 'tt0101540',
 'tt0116320',
 'tt0408790',
 'tt1217209',
 'tt0227445',
 'tt1946502',
 'tt0108358',
 'tt0206275',
 'tt0472126',
 'tt0983193',
 'tt0102526',
 'tt0431197',
 'tt0315297',
 'tt0286788',
 'tt2024469',
 'tt0091149',
 'tt03

In [7]:
# create the base url for the Open Movie Database (OMDB) API calls
omdb_url = f"http://www.omdbapi.com/?apikey={api_key_omdb}&"

In [9]:
# create a dataframe to hold the OMDB data
gbh_df = pd.DataFrame(columns = ["Title", "Year", "Rated","Released", "Runtime",
                         "Genre", "Language", "Awards", "Metascore", "imdbRating", 
                         "imdbVotes", "imdbID", "Type", "BoxOffice", "Production"])

# initialize the count, will stop the loop when the count reaches 600
i=0


for id in call_ids:
    gbh_imdb = f"i={id}"
    print(gbh_imdb)
    try:
        response_json = requests.get(omdb_url + gbh_imdb + '&type=movie').json()
        print(response_json)
        year = int(response_json['Year'][0:4])
        type_m = response_json['Type']
        country = response_json['Country'].find('USA')
#         valid_ids.append(id)
        if (year >= 1990) & (type_m == 'movie') & (country >= 0):
            print('This meets the Criteria!')
            movie_title = response_json['Title']
            rated = response_json['Rated']
            released = response_json['Released']
            runtime = response_json['Runtime']
            genre = response_json['Genre']
            language = response_json['Language']
            awards = response_json['Awards']
            metascore = response_json['Metascore']
            imdb_rating = response_json['imdbRating']
            imdb_votes = response_json['imdbVotes']
            imdb_id = response_json['imdbID']
            box_office = response_json['BoxOffice']
            production = response_json['Production']
            gbh_df = gbh_df.append({"Title": movie_title, 
                                      "Year": year, 
                                      "Rated": rated,
                                      "Released": released,
                                      "Runtime": runtime, 
                                      "Genre": genre, 
                                      "Language": language,
                                      "Awards": awards,
                                      "Metascore": metascore,
                                      "imdbRating": imdb_rating, 
                                      "imdbVotes": imdb_votes,
                                      "imdbID": imdb_id,
                                      "Type": type_m,
                                      "BoxOffice": box_office,
                                      "Production": production}, ignore_index = True)

            i+=1
            if i >= 600:
                break
        else:
            print(f'Criteria Failed: year: {year}, type: {type_m}, USA? {country}')

    except KeyError:
        print(f'{id} not found')
        pass


gbh_df

i=tt0071853
{'Title': 'Monty Python and the Holy Grail', 'Year': '1975', 'Rated': 'PG', 'Released': '25 May 1975', 'Runtime': '91 min', 'Genre': 'Adventure, Comedy, Fantasy', 'Director': 'Terry Gilliam, Terry Jones', 'Writer': 'Graham Chapman, John Cleese, Eric Idle, Terry Gilliam, Terry Jones, Michael Palin', 'Actors': 'Graham Chapman, John Cleese, Eric Idle, Terry Gilliam', 'Plot': 'King Arthur (Graham Chapman) and his Knights of the Round Table embark on a surreal, low-budget search for the Holy Grail, encountering many, very silly obstacles.', 'Language': 'English, French, Latin', 'Country': 'UK', 'Awards': '2 wins & 2 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BN2IyNTE4YzUtZWU0Mi00MGIwLTgyMmQtMzQ4YzQxYWNlYWE2XkEyXkFqcGdeQXVyNjU0OTQ0OTY@._V1_SX300.jpg', 'Ratings': [{'Source': 'Internet Movie Database', 'Value': '8.2/10'}, {'Source': 'Rotten Tomatoes', 'Value': '97%'}, {'Source': 'Metacritic', 'Value': '93/100'}], 'Metascore': '93', 'imdbRating': '8.2', 'imdbVo

{'Title': 'The Girlfriend Experience', 'Year': '2009', 'Rated': 'R', 'Released': '08 Jul 2009', 'Runtime': '77 min', 'Genre': 'Drama', 'Director': 'Steven Soderbergh', 'Writer': 'David Levien, Brian Koppelman', 'Actors': 'Sasha Grey, Chris Santos, Philip Eytan, Colby Trane', 'Plot': 'A drama set in the days leading up to the 2008 Presidential election, and centered on a high-end Manhattan call girl meeting the challenges of her boyfriend, her clients, and her work.', 'Language': 'English, French', 'Country': 'USA', 'Awards': '1 nomination.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BMjE5OTY5MDIzM15BMl5BanBnXkFtZTcwNTU4NzQ0Mg@@._V1_SX300.jpg', 'Ratings': [{'Source': 'Internet Movie Database', 'Value': '5.5/10'}, {'Source': 'Rotten Tomatoes', 'Value': '67%'}, {'Source': 'Metacritic', 'Value': '66/100'}], 'Metascore': '66', 'imdbRating': '5.5', 'imdbVotes': '15,619', 'imdbID': 'tt1103982', 'Type': 'movie', 'DVD': '29 Sep 2009', 'BoxOffice': '$642,853', 'Production': 'Magnolia Pic

i=tt0207201
{'Title': 'What Women Want', 'Year': '2000', 'Rated': 'PG-13', 'Released': '15 Dec 2000', 'Runtime': '127 min', 'Genre': 'Comedy, Fantasy, Romance', 'Director': 'Nancy Meyers', 'Writer': 'Josh Goldsmith (story), Cathy Yuspa (story), Diane Drake (story), Josh Goldsmith (screenplay), Cathy Yuspa (screenplay)', 'Actors': 'Mel Gibson, Helen Hunt, Marisa Tomei, Alan Alda', 'Plot': 'After an accident, a chauvinistic executive gains the ability to hear what women are really thinking.', 'Language': 'English', 'Country': 'USA', 'Awards': 'Nominated for 1 Golden Globe. Another 5 wins & 8 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BZjUyZWE5YmMtNDA2ZC00NzFlLTg0MzktOTgzYjA2ZWE3NmIwXkEyXkFqcGdeQXVyNDk3NzU2MTQ@._V1_SX300.jpg', 'Ratings': [{'Source': 'Internet Movie Database', 'Value': '6.4/10'}, {'Source': 'Rotten Tomatoes', 'Value': '54%'}, {'Source': 'Metacritic', 'Value': '47/100'}], 'Metascore': '47', 'imdbRating': '6.4', 'imdbVotes': '187,739', 'imdbID': 'tt0207

{'Title': 'The Matrix Revolutions', 'Year': '2003', 'Rated': 'R', 'Released': '05 Nov 2003', 'Runtime': '129 min', 'Genre': 'Action, Sci-Fi', 'Director': 'Lana Wachowski, Lilly Wachowski', 'Writer': 'Lilly Wachowski, Lana Wachowski, Lilly Wachowski (characters), Lana Wachowski (characters)', 'Actors': 'Mary Alice, Tanveer K. Atwal, Helmut Bakaitis, Kate Beahan', 'Plot': 'The human city of Zion defends itself against the massive invasion of the machines as Neo fights to end the war at another front while also opposing the rogue Agent Smith.', 'Language': 'English, French', 'Country': 'USA', 'Awards': '5 wins & 35 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BNzNlZTZjMDctZjYwNi00NzljLWIwN2QtZWZmYmJiYzQ0MTk2XkEyXkFqcGdeQXVyNTAyODkwOQ@@._V1_SX300.jpg', 'Ratings': [{'Source': 'Internet Movie Database', 'Value': '6.8/10'}, {'Source': 'Rotten Tomatoes', 'Value': '35%'}, {'Source': 'Metacritic', 'Value': '47/100'}], 'Metascore': '47', 'imdbRating': '6.8', 'imdbVotes': '435,

i=tt0056197
{'Title': 'The Longest Day', 'Year': '1962', 'Rated': 'G', 'Released': '04 Oct 1962', 'Runtime': '178 min', 'Genre': 'Action, Drama, History, War', 'Director': 'Ken Annakin, Andrew Marton, Gerd Oswald, Bernhard Wicki, Darryl F. Zanuck', 'Writer': 'Cornelius Ryan (screenplay), Cornelius Ryan (book), Romain Gary (additional episodes written by), James Jones (additional episodes written by), David Pursall (additional episodes written by), Jack Seddon (additional episodes written by)', 'Actors': 'Eddie Albert, Paul Anka, Arletty, Jean-Louis Barrault', 'Plot': 'The events of D-Day, told on a grand scale from both the Allied and German points of view.', 'Language': 'English, German, French', 'Country': 'USA', 'Awards': 'Won 2 Oscars. Another 6 wins & 6 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BZTM1ZjQ2YTktNDM2MS00NGY2LTkzNzItZTU4ODg1ODNkMWYxL2ltYWdlXkEyXkFqcGdeQXVyNjc1NTYyMjg@._V1_SX300.jpg', 'Ratings': [{'Source': 'Internet Movie Database', 'Value': '7.8/

...

{'Title': 'The Nun', 'Year': '2018', 'Rated': 'R', 'Released': '07 Sep 2018', 'Runtime': '96 min', 'Genre': 'Horror, Mystery, Thriller', 'Director': 'Corin Hardy', 'Writer': 'Gary Dauberman (screenplay by), James Wan (story by), Gary Dauberman (story by)', 'Actors': 'Demián Bichir, Taissa Farmiga, Jonas Bloquet, Bonnie Aarons', 'Plot': 'A priest with a haunted past and a novice on the threshold of her final vows are sent by the Vatican to investigate the death of a young nun in Romania and confront a malevolent force in the form of a demonic nun.', 'Language': 'English, French, Romanian, Latin', 'Country': 'USA', 'Awards': '2 wins & 1 nomination.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BMjM3NzQ5NDcxOF5BMl5BanBnXkFtZTgwNzM4MTQ5NTM@._V1_SX300.jpg', 'Ratings': [{'Source': 'Internet Movie Database', 'Value': '5.3/10'}, {'Source': 'Rotten Tomatoes', 'Value': '26%'}, {'Source': 'Metacritic', 'Value': '46/100'}], 'Metascore': '46', 'imdbRating': '5.3', 'imdbVotes': '109,994', 'imd

i=tt0383216
{'Title': 'The Pink Panther', 'Year': '2006', 'Rated': 'PG', 'Released': '10 Feb 2006', 'Runtime': '93 min', 'Genre': 'Adventure, Comedy, Crime, Family, Mystery', 'Director': 'Shawn Levy', 'Writer': 'Len Blum (screenplay), Steve Martin (screenplay), Len Blum (story), Michael Saltzman (story), Maurice Richlin (characters), Blake Edwards (characters)', 'Actors': 'Steve Martin, Kevin Kline, Jean Reno, Emily Mortimer', 'Plot': 'Bumbling Inspector Clouseau must solve the murder of a famous soccer coach and find out who stole the infamous Pink Panther diamond.', 'Language': 'English', 'Country': 'USA, Czech Republic', 'Awards': '1 win & 8 nominations.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BNGI2MjVlNzEtZDg1ZS00MGU1LWFhNTQtNzMwZDViOWRkNzhkXkEyXkFqcGdeQXVyNTIzOTk5ODM@._V1_SX300.jpg', 'Ratings': [{'Source': 'Internet Movie Database', 'Value': '5.7/10'}, {'Source': 'Rotten Tomatoes', 'Value': '21%'}, {'Source': 'Metacritic', 'Value': '38/100'}], 'Metascore': '38', 'imdbR

i=tt7111402
{'Title': 'Oxidan', 'Year': '2017', 'Rated': 'N/A', 'Released': '21 Sep 2017', 'Runtime': '93 min', 'Genre': 'Comedy, Drama', 'Director': 'Hamed Mohammadi', 'Writer': 'Hamed Mohammadi', 'Actors': 'Javad Ezati, Amir Jafari, Vahid Aghapoor, Reza Behbudi', 'Plot': "Aslan's fiance Negar is going abroad the country illegally and without informing him at all. Now he is after a way to get a visa and go gets her back.", 'Language': 'Persian', 'Country': 'Iran', 'Awards': 'N/A', 'Poster': 'https://m.media-amazon.com/images/M/MV5BMTY5YWM4ODItMzY1ZS00YTE4LWFiNzAtNWQxODFjYmJjN2MzXkEyXkFqcGdeQXVyNjkxOTM4ODY@._V1_SX300.jpg', 'Ratings': [{'Source': 'Internet Movie Database', 'Value': '5.3/10'}], 'Metascore': 'N/A', 'imdbRating': '5.3', 'imdbVotes': '1,177', 'imdbID': 'tt7111402', 'Type': 'movie', 'DVD': 'N/A', 'BoxOffice': 'N/A', 'Production': 'Filmsazan Cooperation', 'Website': 'N/A', 'Response': 'True'}
Criteria Failed: year: 2017, type: movie, USA? -1
i=tt0104454
{'Title': 'Howards End

{'Title': 'The Tie That Binds', 'Year': '1995', 'Rated': 'R', 'Released': '08 Sep 1995', 'Runtime': '99 min', 'Genre': 'Crime, Drama, Thriller', 'Director': 'Wesley Strick', 'Writer': 'Michael Auerbach', 'Actors': 'Daryl Hannah, Keith Carradine, Moira Kelly, Vincent Spano', 'Plot': 'John Netherwood and his wife Leann are fugitives who are both wanted for murder. They have a young daughter named Janie. John and Leann are in the process of robbing a house when the two ...', 'Language': 'English', 'Country': 'USA', 'Awards': '1 nomination.', 'Poster': 'https://m.media-amazon.com/images/M/MV5BZDE2Njg0YmEtN2Q1Yi00MzQ3LTkzODQtNjkxMGEzNzVkMjIzXkEyXkFqcGdeQXVyNjMwMjk0MTQ@._V1_SX300.jpg', 'Ratings': [{'Source': 'Internet Movie Database', 'Value': '5.0/10'}, {'Source': 'Rotten Tomatoes', 'Value': '8%'}], 'Metascore': 'N/A', 'imdbRating': '5.0', 'imdbVotes': '1,069', 'imdbID': 'tt0114666', 'Type': 'movie', 'DVD': '11 Apr 2000', 'BoxOffice': 'N/A', 'Production': 'Buena Vista', 'Website': 'N/A', 'R

Title  Year  Rated     Released  Runtime  \
0                Vulgar  2000      R  26 Apr 2002   87 min   
1    Out of the Furnace  2013      R  06 Dec 2013  116 min   
2           Coyote Ugly  2000  PG-13  04 Aug 2000  100 min   
3     Parental Guidance  2012     PG  25 Dec 2012  105 min   
4         Raising Helen  2004  PG-13  28 May 2004  119 min   
..                  ...   ...    ...          ...      ...   
595                Life  2017      R  24 Mar 2017  104 min   
596               Filth  2013      R  24 Apr 2014   97 min   
597         Masterminds  2016  PG-13  30 Sep 2016   95 min   
598           Planet 51  2009     PG  20 Nov 2009   91 min   
599            Catwoman  2004  PG-13  23 Jul 2004  104 min   

                                            Genre  \
0                          Crime, Drama, Thriller   
1                  Action, Crime, Drama, Thriller   
2                   Comedy, Drama, Music, Romance   
3                                  Comedy, Family   
4                          Comedy, Drama, Romance   
..                                            ...   
595                      Horror, Sci-Fi, Thriller   
596                          Comedy, Crime, Drama   
597                      Biography, Comedy, Crime   
598  Animation, Adventure, Comedy, Family, Sci-Fi   
599                        Action, Crime, Fantasy   

                          Language                    Awards Metascore  \
0                          English                       N/A         5   
1                          English   2 wins & 9 nominations.        63   
2                          English   4 wins & 8 nominations.        27   
3                          English    1 win & 4 nominations.        36   
4                          English             1 nomination.        38   
..                             ...                       ...       ...   
595  English, Japanese, Vietnamese            7 nominations.        54   
596         English, German, Scots  9 wins & 14 nominations.        56   
597               English, Spanish             1 nomination.        47   
598               English, Spanish   4 wins & 4 nominations.        39   
599               English, Spanish  13 wins & 8 nominations.        27   

    imdbRating imdbVotes     imdbID   Type    BoxOffice  \
0          5.3     3,876  tt0120467  movie          N/A   
1          6.8   103,339  tt1206543  movie   $8,314,341   
2          5.7   104,644  tt0200550  movie          N/A   
3          6.0    24,453  tt1047540  movie  $77,253,083   
4          6.0    34,868  tt0350028  movie  $37,379,556   
..         ...       ...        ...    ...          ...   
595        6.6   199,775  tt5442430  movie  $30,180,466   
596        7.1    98,589  tt1450321  movie      $23,145   
597        5.8    48,784  tt2461150  movie  $17,356,894   
598        6.0    49,599  tt0762125  movie  $42,194,060   
599        3.4   107,522  tt0327554  movie  $40,200,000   

                         Production  
0                  Lions Gate Films  
1                  Relativity Media  
2                       Buena Vista  
3                  20th Century Fox  
4              Buena Vista Pictures  
..                              ...  
595                  Skydance Films  
596                Magnet Releasing  
597                Relativity Media  
598  Sony Pictures/TriStar Pictures  
599           Warner Bros. Pictures  

[600 rows x 15 columns]

In [10]:
tmdb_called_df = tmdb_data_clean_df.loc[tmdb_data_clean_df['IMDB ID'].isin(gbh_df['imdbID'].to_list())]
tmdb_called_df

Budget     IMDB ID    Revenue
43     1500000   tt0100053    5585154
44    10000000   tt0099739   47410000
58    30000000   tt0099810  200512643
74    11000000   tt0099329    8266343
92     1000000   tt0099939    2554476
...        ...         ...        ...
5445     50000  tt10521814     359377
5447  25000000   tt4916630   50401502
5462  33000000   tt8688634   47088457
5469  10000000   tt5563334   33256058
5475  45000000   tt3513548   33904605

[600 rows x 3 columns]

In [11]:
movie_df = pd.merge(gbh_df, tmdb_called_df, how='outer', left_on='imdbID', right_on='IMDB ID')

movie_df

Title  Year  Rated     Released  Runtime  \
0                Vulgar  2000      R  26 Apr 2002   87 min   
1    Out of the Furnace  2013      R  06 Dec 2013  116 min   
2           Coyote Ugly  2000  PG-13  04 Aug 2000  100 min   
3     Parental Guidance  2012     PG  25 Dec 2012  105 min   
4         Raising Helen  2004  PG-13  28 May 2004  119 min   
..                  ...   ...    ...          ...      ...   
595                Life  2017      R  24 Mar 2017  104 min   
596               Filth  2013      R  24 Apr 2014   97 min   
597         Masterminds  2016  PG-13  30 Sep 2016   95 min   
598           Planet 51  2009     PG  20 Nov 2009   91 min   
599            Catwoman  2004  PG-13  23 Jul 2004  104 min   

                                            Genre  \
0                          Crime, Drama, Thriller   
1                  Action, Crime, Drama, Thriller   
2                   Comedy, Drama, Music, Romance   
3                                  Comedy, Family   
4                          Comedy, Drama, Romance   
..                                            ...   
595                      Horror, Sci-Fi, Thriller   
596                          Comedy, Crime, Drama   
597                      Biography, Comedy, Crime   
598  Animation, Adventure, Comedy, Family, Sci-Fi   
599                        Action, Crime, Fantasy   

                          Language                    Awards Metascore  \
0                          English                       N/A         5   
1                          English   2 wins & 9 nominations.        63   
2                          English   4 wins & 8 nominations.        27   
3                          English    1 win & 4 nominations.        36   
4                          English             1 nomination.        38   
..                             ...                       ...       ...   
595  English, Japanese, Vietnamese            7 nominations.        54   
596         English, German, Scots  9 wins & 14 nominations.        56   
597               English, Spanish             1 nomination.        47   
598               English, Spanish   4 wins & 4 nominations.        39   
599               English, Spanish  13 wins & 8 nominations.        27   

    imdbRating imdbVotes     imdbID   Type    BoxOffice  \
0          5.3     3,876  tt0120467  movie          N/A   
1          6.8   103,339  tt1206543  movie   $8,314,341   
2          5.7   104,644  tt0200550  movie          N/A   
3          6.0    24,453  tt1047540  movie  $77,253,083   
4          6.0    34,868  tt0350028  movie  $37,379,556   
..         ...       ...        ...    ...          ...   
595        6.6   199,775  tt5442430  movie  $30,180,466   
596        7.1    98,589  tt1450321  movie      $23,145   
597        5.8    48,784  tt2461150  movie  $17,356,894   
598        6.0    49,599  tt0762125  movie  $42,194,060   
599        3.4   107,522  tt0327554  movie  $40,200,000   

                         Production     Budget    IMDB ID    Revenue  
0                  Lions Gate Films     120000  tt0120467      14904  
1                  Relativity Media   22000000  tt1206543   15400000  
2                       Buena Vista   45000000  tt0200550  113916474  
3                  20th Century Fox   25000000  tt1047540  119772232  
4              Buena Vista Pictures   50000000  tt0350028   49718611  
..                              ...        ...        ...        ...  
595                  Skydance Films   58000000  tt5442430  100541806  
596                Magnet Releasing    5000000  tt1450321    9114264  
597                Relativity Media   25000000  tt2461150   29200000  
598  Sony Pictures/TriStar Pictures   70000000  tt0762125  104945765  
599           Warner Bros. Pictures  100000000  tt0327554   82102379  

[600 rows x 18 columns]

In [12]:
movie_df['Title'].value_counts()

The Lion King                          2
Airborne                               1
The Tigger Movie                       1
Star Trek                              1
Hellraiser: Bloodline                  1
                                      ..
Vulgar                                 1
A Single Man                           1
Captain America: The Winter Soldier    1
The Spiderwick Chronicles              1
The Help                               1
Name: Title, Length: 599, dtype: int64

In [13]:
test_df = movie_df.loc[movie_df['Title'] == 'The Lion King']
test_df

Title  Year Rated     Released  Runtime  \
505  The Lion King  2019    PG  19 Jul 2019  118 min   
523  The Lion King  1994     G  24 Jun 1994   88 min   

                                            Genre  \
505  Animation, Adventure, Drama, Family, Musical   
523  Animation, Adventure, Drama, Family, Musical   

                                  Language  \
505  English, Xhosa, Zulu, French, Spanish   
523          English, Swahili, Xhosa, Zulu   

                                                Awards Metascore imdbRating  \
505  Nominated for 1 Oscar. Another 16 wins & 34 no...        55        6.9   
523    Won 2 Oscars. Another 35 wins & 34 nominations.        88        8.5   

    imdbVotes     imdbID   Type    BoxOffice            Production     Budget  \
505   194,149  tt6105098  movie          N/A  Walt Disney Pictures  260000000   
523   907,281  tt0110357  movie  $94,240,635           Buena Vista   45000000   

       IMDB ID     Revenue  
505  tt6105098  1656943394  
523  tt0110357   763455561

In [14]:
movie_df['BoxOffice'].value_counts()

N/A             250
$80,200,000       2
$31,494,270       1
$50,092           1
$13,850,403       1
               ... 
$19,548,064       1
$300,000          1
$101,555,644      1
$399,611          1
$8,314,341        1
Name: BoxOffice, Length: 350, dtype: int64

In [15]:
output_data_file = os.path.join('data_files','good_merged_data.csv')
# Open the csv file for writing
with open(output_data_file, 'w', encoding='utf-8', newline='\n') as csvfile:

    # write the DataFrame data to the csv file
    movie_df.to_csv(csvfile, index=False)

# Close the csv file
csvfile.close()